# Application of Dask on Paralled Optimisation and Parameter Tunning

## Introduction

1. Recap
    - Multithreading and Multiprocessing
    - Dask
2. Application of Dask on Convex Optimisation on Larger-Than-Memory Arrays/Data

## Application of Dask on Larger-Than-Memory Optimisation 

### Multithreading and Multiprocessing

**Multithreading:**
- A new thread is spawned within the existing process.
- Starting a thread is faster than starting a process.
- Memory is shared between all threads.
- Give parallel computing capabilities in multi core CPUs.
- Mutexes often necessary to control access to shared data.
- One GIL for all threads.

**Multiprocessing:**
- A new process is started independent of the first process.
- Starting a process is slower than starting a thread.
- Memory is not shared between processes. 
- Give parallel computing capabilities in multi core CPUs.
- Mutexes not necessary (unless threading in the new process).
- One GIL for each process.

### Dask

In previous tutorial, we have introduced basic concepts of Dask and its high-level and low-level implementations.

Here is a quick recap:


1. **High level**: 

    dask.array/dask.dataframe -> Partition Large Datasets/Arrays to smaller parts
    
    
    

2. **Low level**: 

    *1) Delayed*: 
    It will make functions into tasks and put the task graph to keep a track of all the functions that are dependent on the previous task. The task tree will be lazy meaning that it has to be `.compute()` to execute the function over the task tree and give the result.
        
    *2) Futures*:
    When you want to ask the scheduler to run something. You can submit the task, and the `submit()` function returns a `Future`. Then, you can redeem your future by a `results()`. It underlies high-level implementations of Dask.

### Application of Dask on Convex Optimisation on Larger-Than-Memory Arrays/Data


This code example is taken from [Developing Convex Optimization Algorithms in Dask - parallel math is fun](https://blog.dask.org/2017/03/22/dask-glm-1) supported by Continuum Analytics, the XDATA Program, and the Data Driven Discovery Initiative from the Moore Foundation.

Motivation: sometimes we have extemely large matrix calculation to be done and potentially large convex optimisation problems. Dask is a powerful tool in this case because it is capable to handle workload that is way higher than the system memory we have.

The following is a toy example to demonstrate this.

Let's imagine that we have a very large dataset ($10,000,000 \times 400$) with 400 features, and we want to fit a linear model with just slope coefficients.

This will be a very easy convex optimisation problem:
    
$$
\min_{\beta} \|y - X\beta\|_2
$$

In [1]:
import dask
import dask.array as da
import numpy as np

from dask.distributed import Client

client = Client()

client

<Client: 'tcp://127.0.0.1:49449' processes=4 threads=8, memory=16.00 GiB>

In [2]:
## create inputs with a bunch of independent normals
β = np.random.random(400)  # random beta coefficients, no intercept
X = da.random.normal(0, 1, size=(10000000, 400), chunks=(100000, 400))
y = X.dot(β) + da.random.normal(0, 1, size=10000000, chunks= (10000000))

Things to consider when sizing:

1. The size of the chunk
2. The imbalance among chunks
3. The total size of chunks

In [3]:
#X, y = dask.persist(X, y)

In [4]:
X

dask.array<normal, shape=(10000000, 400), dtype=float64, chunksize=(100000, 400), chunktype=numpy.ndarray>

In [5]:
y

dask.array<add, shape=(10000000,), dtype=float64, chunksize=(100000,), chunktype=numpy.ndarray>

With the closed-formed solution, we want to solve the $\beta^*$ where
$$
\beta^* = \left(X^T X\right)^{-1} X^T y
$$

In [6]:
β_star = da.linalg.solve(X.T.dot(X), X.T.dot(y))

In [7]:
β_star.visualize()

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.647659 to fit


In [8]:
%time abs(β_star.compute() - β).max()

CPU times: user 1.49 s, sys: 329 ms, total: 1.81 s
Wall time: 27.3 s


0.0011812629482232315

Next, We will unreval the delayed function using an example of a lasso regression.

In this case we would like to conduct the following optimisation problem:

$$
\min_{\beta} \|y - X\beta\|_2^2 + \lambda \|\beta\|_1
$$

Here we use [alternating direction method of multipliers](https://stanford.edu/~boyd/admm.html) [ADMM], which breaks the optimisations into smaller pieces and do the optimisation on each chunck.

The above lasso problem can be seen as


$$\begin{array}{ll}\operatorname{minimize} & l(x)+g(z) \\ \text { subject to } & x-z=0\end{array}$$

where $g(z)=\lambda\|z\|_1$. By augmented Lagrangian, the algorithm is

$$
\begin{aligned}
x^{k+1} &:=\underset{x}{\operatorname{argmin}}\left(l(x)+(\rho / 2)\left\|x-z^k+u^k\right\|_2^2\right) \\
z^{k+1} &:=S_{\lambda / \rho}\left(x^{k+1}+u^k\right) \\
u^{k+1} &:=u^k+x^{k+1}-z^{k+1} .
\end{aligned}
$$

(Boyd et al., 2011)

There are more details in the ADMM and consensus. You can find more information in [Boyd et al., 2011](https://www.nowpublishers.com/article/Details/MAL-016).


In [9]:
def local_f(β, X, y, z, u, ρ):
    """
        β: Slope Coefficient
        X: Attributes
        y: Response
        z: Consensus estimate
        u: Dual variable (β_hat - z)
        ρ: Step size
    """
    return ((y - X.dot(β))**2).sum() + (ρ / 2) * np.dot(β - z + u, β - z + u)

def local_grad(β, X, y, z, u, ρ):
    return 2 * X.T.dot(X.dot(β) - y) + ρ * (β - z + u)


For the $z$, $L1$ is convex but not differentiable at $x=0$ so we use soft-thersholding operator:
$$
\beta_i^*=S_{\alpha / \lambda}\left(\hat{\beta}_i\right)=\operatorname{sign}\left(\hat{\beta}_i\right) \max \left(\left|\hat{\beta}_i\right|-\alpha \lambda, 0\right)
$$

In [10]:
def shrinkage(β, t):
    """
    β: ztilde -> consensus estimate
    t: λ / (ρ * Npartitions)
    """
    return np.maximum(0, β - t) - np.maximum(0, -β - t)

This function is from [dask-glm](https://github.com/dask/dask-glm), which calculates the local minimum using the [L-BFGS-B algorithm](https://en.wikipedia.org/wiki/Limited-memory_BFGS#L-BFGS-B).


In [11]:
from scipy.optimize import fmin_l_bfgs_b
def local_update(X, y, β, z, u, ρ, f, fprime, solver=fmin_l_bfgs_b):

    β = β.ravel()
    u = u.ravel()
    z = z.ravel()
    solver_args = (X, y, z, u, ρ)
    β, f, d = solver(f, β, fprime=fprime, args=solver_args,
                        maxiter=200,
                        maxfun=250)

    return β

After the local optimisation has been run, we will have estimation for each partition in the Dask Array and we update $\beta$ across chunks.


In [12]:
## set some algorithm parameters
max_steps = 5
λ = 7.2
ρ = 1.0

(n, p) = X.shape
nchunks = X.npartitions

XD = X.to_delayed().flatten().tolist()  # A list of pointers to remote numpy arrays
yD = y.to_delayed().flatten().tolist()  # ... one for each chunk

We can see XD is a list of `Delayed` objects, which keeps a track of all the functions in hand. It is because it is a part of the task graph.

In [13]:
XD

[Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 0, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 1, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 2, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 3, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 4, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 5, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 6, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 7, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 8, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 9, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 10, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 11, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 12, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 13, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 14, 0)),
 Delayed(('normal-419e9b26975c52769fc2fa4f912f0947', 15, 0)),
 Delayed(('normal-

In [14]:
# the initial consensus estimate
z = np.zeros(p)

# an array of the individual "dual variables" and parameter estimates,
# one for each chunk of data
u = np.array([np.zeros(p) for i in range(nchunks)])
βs = np.array([np.zeros(p) for i in range(nchunks)])

for k in range(max_steps):

    ### Step 1 of ADMM
    new_βs = [dask.delayed(local_update)(xx, yy, bb, z, uu, ρ,
                                            f=local_f,
                                            fprime=local_grad)
                 for xx, yy, bb, uu in zip(XD, yD, βs, u)]
    new_βs = np.array(dask.compute(*new_βs))
    

    # β_hat will be a weighted sum of local estimate and the consensus estimate.
    β_hat = 0.9 * new_βs + 0.1 * z
    
    
    ### Step 2 of ADMM
    zold = z.copy()
    # ztilde -> concensus of β across local optimisers
    ztilde = np.mean(β_hat + np.array(u), axis=0)
    
    # λ / (ρ * nchunks) is the shrinkage term
    z = shrinkage(ztilde, λ / (ρ * nchunks))
    print(f'Iteration {k+1}, {(z == 0).sum()} coefficients are zeroed out')
    
    
    ### Step 3 of ADMM
    u += β_hat - z


Iteration 1, 32 coefficients are zeroed out
Iteration 2, 11 coefficients are zeroed out
Iteration 3, 10 coefficients are zeroed out
Iteration 4, 9 coefficients are zeroed out
Iteration 5, 5 coefficients are zeroed out


We did not specify a converge criteria due to the runtime. But a criteria can be found in [Boyd et al., 2011](https://www.nowpublishers.com/article/Details/MAL-016).

More to look at: [GPU acceleration of ADMM](https://www.computer.org/csdl/proceedings-article/sc/2020/999800a795/1oeOTeU71Mk).

There are more interesting application using the same code here but in an [asynchronous manner](https://blog.dask.org/2017/04/19/dask-glm-2).